# Problem 10.3: Controlling p53 levels


<hr>

In [1]:
import collections
import numpy as np

<hr>

[p53](https://en.wikipedia.org/wiki/P53) is an important protein for tumor suppression, DNA damage repair, cell cycle regulation, and more. In their [2012 paper](https://doi.org/10.1126/science.1218351), the researchers in Galit Lahav's group investigated how temporal dynamics of p53 controls cell fate in [MCF-7 cells](https://en.wikipedia.org/wiki/MCF-7), a breast cancer cell line. It had been previously observed that p53 levels oscillate upon exposure to stress due to γ radiation. To instead study how cells respond to sustained levels of p53, the authors controlled p53 levels using the drug Nutlin-3. To do this, they devised a program for adjusting Nutlin-3 levels in the cell culture that would keep the p53 levels at a constant high level. They based this program on a mathematical model of the p53 circuit (shown in the figure below) that they developed and parametrized in an [earlier paper](https://doi.org/10.1016/j.molcel.2008.03.016).

<div style="margin: auto; width: 300px">
    
![p53 circuit](p53_circuit.svg)

</div>

The p53 levels oscillate due to a delays in the autoinhibitory loops mediated by Mdm2 and Wip1. The dynamical equations for this circuit, as presented in the paper, are

\begin{align}
\frac{\mathrm{d}p_i}{\mathrm{d}t} &= \beta_\mathrm{p} - \frac{\delta_\mathrm{mp}^i \, m\,p_i}{1+\left(n(t-\tau_\mathrm{n})/k\right)^{n_\mathrm{n}}} - \beta_\mathrm{sp}\,p_i\,\frac{(s/k_\mathrm{s})^{n_\mathrm{s}}}{1 + (s/k_\mathrm{s})^{n_\mathrm{s}}} - \gamma_\mathrm{p}^i\, p_i,\\[1em]
\frac{\mathrm{d}p_a}{\mathrm{d}t} &=  \beta_\mathrm{sp}\,p_i\,\frac{(s/k_\mathrm{s})^{n_\mathrm{s}}}{1 + (s/k_\mathrm{s})^{n_\mathrm{s}}} - \frac{\delta_\mathrm{mp}^a \, m\,p_a}{1+\left(n(t-\tau_\mathrm{n})/k\right)^{n_\mathrm{n}}},\\[1em]
\frac{\mathrm{d}m}{\mathrm{d}t} &= \beta_{m_i} + \beta_\mathrm{m}\,p_a(t-\tau_\mathrm{m}) - \delta_\mathrm{sm}\,s\,m - \gamma_m\,m,\\[1em]
\frac{\mathrm{d}w}{\mathrm{d}t} &= \beta_\mathrm{w}\,p_a(t-\tau_\mathrm{w}) - \gamma_\mathrm{w}\,w,\\[1em]
\frac{\mathrm{d}s}{\mathrm{d}t} &= \beta_\mathrm{s}\,\theta(t) - \delta_\mathrm{ws}\,s\,\frac{(w/k_\mathrm{w})^{n_\mathrm{w}}}{1 + (w/k_\mathrm{w})^{n_\mathrm{w}}} - \gamma_\mathrm{s}\,s.
\end{align}

Here, $p_i$ and $p_a$ denote the concentrations of inactive and active p53, respectively. The variables $m$ and $w$ respectively represent the concentrations of Mdm2 and Wip1. The concentration of the DNA damage signal is denoted as $s$. Finally, $n$ is the externally imposed concentration of Nutlin-3. The function $\theta(t)$ is the Heaviside function,

\begin{align}
\theta(t) = \left\{\begin{array}[ll] 00 &  t < 0 \\
1 &  t \ge 0.
\end{array}
\right.
\end{align}

The parameters for the model are given in the code cell below as a named tuple for convenience. The units of all parameters are such that time is in hours and concentrations in micromolar. Before proceeding, take a moment and make sure you understand the physical meaning of each term in the equations.

In [2]:
Params = collections.namedtuple(
    "Params",
    [
        "delta_mpi",
        "gamma_pi",
        "delta_mpa",
        "delta_sm",
        "gamma_m",
        "gamma_w",
        "delta_ws",
        "gamma_s",
        "beta_p",
        "beta_sp",
        "beta_m",
        "beta_mi",
        "beta_w",
        "beta_s",
        "tau_n",
        "tau_m",
        "tau_w",
        "k",
        "n_n",
        "n_s",
        "n_w",
        "k_w",
        "k_s",
    ],
)

params = Params(
    delta_mpi=5,
    gamma_pi=2,
    delta_mpa=1.4,
    delta_sm=0.5,
    gamma_m=1,
    gamma_w=0.7,
    delta_ws=50,
    gamma_s=7.5,
    beta_p=0.9,
    beta_sp=10,
    beta_m=0.9,
    beta_mi=0.2,
    beta_w=0.25,
    beta_s=10,
    tau_n=0.4,
    tau_m=0.7,
    tau_w=1.25,
    k=2.3,
    n_n=3.3,
    n_s=4,
    n_w=4,
    k_w=0.2,
    k_s=1,
)

**a)** Solve the equations numerically with $n = 0$. Plot the solution along with the experimental measurements from the [Purvis, et al. paper](https://doi.org/10.1126/science.1218351), given in the Numpy arrays below. This helps verify that the model gives results similar to what you would observe experimentally.

In [3]:
# Time points (in units of hours)
time = np.array([0, 1, 2, 3, 4, 5, 6, 7, 8, 12])

# p53 concentration
relative_total_p53_conc = np.array(
    [0.13, 0.69, 1.00, 0.87, 0.60, 0.35, 0.34, 0.54, 0.61, 0.42]
)

**b)** Come up with a program for controlling the Nutlin-3 concentration so as to bring the total p53 level to a sustained value similar to that of its maximum value during oscillations in the absence of Nutlin-3. I.e., choose a function $N(t)$ to give a sustained level of p53 that is approximately unity (in the units specified by the parameter values). You might want to consider experimental constraints; for example that you might want to have only a few steps where the Nutlin-3 concentrations are adjusted to ease experimentation. Show a plot verifying that your scheme works.

<br />